In [1]:
import pandas as pd
import matplotlib as mpl
import matplotlib.pyplot as plt
import numpy as np
import math as mt
import seaborn as sns
from datetime import date, time, datetime, timedelta
from IPython.display import clear_output
import scipy.stats as ss
from statistics import mode
import os
import sys
import multiprocessing as mp
from sklearn.preprocessing import StandardScaler
from sklearn.preprocessing import Normalizer
from sklearn.linear_model import LinearRegression
from sklearn.ensemble import IsolationForest

In [2]:
cw_directory = os.getcwd()

growth_data_path = f"{cw_directory}//growth_db.csv"
weather_data_path = f"{cw_directory}//weather_db.csv"
zone_data_path = f"{cw_directory}//zone_db.csv"
    
growth_data = pd.read_csv(growth_data_path)
weather_data = pd.read_csv(weather_data_path)
zone_data = pd.read_csv(zone_data_path)

In [3]:
pd.options.display.max_columns = None
pd.options.display.max_rows = None

In [4]:
linearisation_coef = 0.625
stripping_coef = 0.92
min_grow_temp = 3
max_grow_temp = 27
future_days = 20
season = datetime(2021, 1, 1)

In [5]:
weather_data['date'] = pd.to_datetime(weather_data['date'], format='%d/%m/%Y')
weather_data['time'] = pd.to_datetime(weather_data['time'], format='%H:%M:%S')
weather_data['day'] = weather_data.date.dt.day
weather_data['month'] = weather_data.date.dt.month
weather_data['day_month'] = weather_data['day'].astype(str) + " - " + weather_data['month'].astype(str)

weather_data['heat_units'] = weather_data['avg_temp'] - min_grow_temp
weather_data['heat_units'] = np.where((weather_data['heat_units'] < 0), 0, weather_data['heat_units'])
weather_data['heat_units'] = np.where((weather_data['heat_units'] > 24), 24, weather_data['heat_units']/24)

In [6]:
weather_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 65823 entries, 0 to 65822
Data columns (total 16 columns):
 #   Column           Non-Null Count  Dtype         
---  ------           --------------  -----         
 0   date             65823 non-null  datetime64[ns]
 1   time             65823 non-null  datetime64[ns]
 2   avg_temp         65823 non-null  float64       
 3   rh               65823 non-null  float64       
 4   rain             65823 non-null  float64       
 5   solar_radiation  65823 non-null  float64       
 6   wind_speed_avg   65823 non-null  float64       
 7   wind_speed_gust  9591 non-null   float64       
 8   soil_temp        9591 non-null   float64       
 9   bat_volt         65823 non-null  float64       
 10  leaf_wet         60962 non-null  float64       
 11  dew_point        60962 non-null  float64       
 12  day              65823 non-null  int64         
 13  month            65823 non-null  int64         
 14  day_month        65823 non-null  objec

In [7]:
weather_data.head()

date                time  avg_temp    rh  rain  solar_radiation  \
0 2014-05-14 1900-01-01 14:00:00      15.8  55.9   0.0            457.0   
1 2014-05-14 1900-01-01 15:00:00      17.0  51.2   0.0           1212.0   
2 2014-05-14 1900-01-01 16:00:00      17.3  48.9   0.0            862.0   
3 2014-05-14 1900-01-01 17:00:00      17.5  48.9   0.0            611.0   
4 2014-05-14 1900-01-01 18:00:00      16.8  51.0   0.0            232.0   

   wind_speed_avg  wind_speed_gust  soil_temp  bat_volt  leaf_wet  dew_point  \
0             2.7              NaN        NaN    6904.0       0.0        7.2   
1             2.2              NaN        NaN    6952.0       0.0        7.0   
2             2.1              NaN        NaN    6922.0       0.0        6.6   
3             2.0              NaN        NaN    6904.0       0.0        6.7   
4             1.7              NaN        NaN    6894.0       0.0        6.7   

   day  month day_month  heat_units  
0   14      5    14 - 5    0.533333  
1   14      5    14 - 5    0.583333  
2   14      5    14 - 5    0.595833  
3   14      5    14 - 5    0.604167  
4   14      5    14 - 5    0.575000

In [8]:
growth_data['sample_date'] = pd.to_datetime(growth_data['sample_date'], format='%d/%m/%Y')
growth_data['fieldzone'] = growth_data["field"] + " - " + growth_data["zone"].astype(str)
growth_data['stripped_diameter'] = growth_data['diameter'] * stripping_coef

In [9]:
growth_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 131776 entries, 0 to 131775
Data columns (total 6 columns):
 #   Column             Non-Null Count   Dtype         
---  ------             --------------   -----         
 0   sample_date        131776 non-null  datetime64[ns]
 1   field              131776 non-null  object        
 2   zone               131776 non-null  int64         
 3   diameter           131776 non-null  float64       
 4   fieldzone          131776 non-null  object        
 5   stripped_diameter  131776 non-null  float64       
dtypes: datetime64[ns](1), float64(2), int64(1), object(2)
memory usage: 6.0+ MB


In [10]:
growth_data.head()

sample_date      field  zone  diameter      fieldzone  stripped_diameter
0  2019-07-17  Allans 18     1       4.0  Allans 18 - 1               3.68
1  2019-07-17  Allans 18     1       3.0  Allans 18 - 1               2.76
2  2019-07-17  Allans 18     1       5.0  Allans 18 - 1               4.60
3  2019-07-17  Allans 18     1       5.0  Allans 18 - 1               4.60
4  2019-07-17  Allans 18     1       3.0  Allans 18 - 1               2.76

In [11]:
zone_data['planting_date'] = pd.to_datetime(zone_data['planting_date'], format='%d/%m/%Y')
zone_data['harvest_date'] = pd.to_datetime(zone_data['harvest_date'], format='%d/%m/%Y')
zone_data['zone'] = zone_data['zone'].astype(int)
zone_data["fieldzone"] = zone_data["field"] + " - " + zone_data["zone"].astype(str)
zone_data["fieldvariety"] = zone_data["field"] + " - " + zone_data["variety"]

In [12]:
zone_data.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 755 entries, 0 to 754
Data columns (total 15 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   field           755 non-null    object        
 1   zone            755 non-null    int32         
 2   planting_date   755 non-null    datetime64[ns]
 3   variety         755 non-null    object        
 4   method          755 non-null    object        
 5   inputs          755 non-null    object        
 6   protection      755 non-null    object        
 7   planting_rate   755 non-null    int64         
 8   sand            755 non-null    int64         
 9   silt            755 non-null    int64         
 10  clay            755 non-null    int64         
 11  organic_matter  755 non-null    float64       
 12  harvest_date    565 non-null    datetime64[ns]
 13  fieldzone       755 non-null    object        
 14  fieldvariety    755 non-null    object        
dtypes: dat

In [13]:
zone_data.head()

field  zone planting_date  variety   method        inputs protection  \
0  Allans 07     1    2019-04-01  Krypton  Drilled  Conventional     Barley   
1  Allans 07     2    2019-04-01  Krypton  Drilled  Conventional     Barley   
2  Allans 07     3    2019-04-01  Longton  Drilled  Conventional     Barley   
3  Allans 07     4    2019-04-01  Longton  Drilled  Conventional     Barley   
4  Allans 07     5    2019-04-01   Batter  Drilled  Conventional     Barley   

   planting_rate  sand  silt  clay  organic_matter harvest_date  \
0         249820    39    37    24            29.6   2019-12-15   
1         249820    39    37    24            29.6   2019-12-15   
2         256524    39    37    24            29.6   2019-12-15   
3         256524    39    37    24            29.6   2019-12-15   
4         247048    39    37    24            29.6   2019-12-15   

       fieldzone         fieldvariety  
0  Allans 07 - 1  Allans 07 - Krypton  
1  Allans 07 - 2  Allans 07 - Krypton  
2  Allans 07 - 3  Allans 07 - Longton  
3  Allans 07 - 4  Allans 07 - Longton  
4  Allans 07 - 5   Allans 07 - Batter

In [14]:
summary_data = growth_data.copy()

summary_data["zone"] = summary_data["zone"].astype(str)
summary_data["fieldzone"] = summary_data["field"] + " - " + summary_data["zone"]
summary_data['fieldzonedate'] = summary_data['fieldzone'] + " - " + summary_data['sample_date'].astype(str)

summary_data = summary_data.set_index('fieldzone')
summary_data = summary_data.join(zone_data.set_index('fieldzone'), rsuffix = '_join')

summary_data['fieldvarietydate'] = summary_data['fieldvariety'] + " - " + summary_data['sample_date'].astype(str)
summary_data['heat_units'] = 0
summary_data['solar_radiation'] = 0

summary_data.info()

<class 'pandas.core.frame.DataFrame'>
Index: 131776 entries, Allans 06 - 1 to Wissey O (S) - 3
Data columns (total 23 columns):
 #   Column             Non-Null Count   Dtype         
---  ------             --------------   -----         
 0   sample_date        131776 non-null  datetime64[ns]
 1   field              131776 non-null  object        
 2   zone               131776 non-null  object        
 3   diameter           131776 non-null  float64       
 4   stripped_diameter  131776 non-null  float64       
 5   fieldzonedate      131776 non-null  object        
 6   field_join         131776 non-null  object        
 7   zone_join          131776 non-null  int32         
 8   planting_date      131776 non-null  datetime64[ns]
 9   variety            131776 non-null  object        
 10  method             131776 non-null  object        
 11  inputs             131776 non-null  object        
 12  protection         131776 non-null  object        
 13  planting_rate      131776 n

In [15]:
summary_data.head()

sample_date      field zone  diameter  stripped_diameter  \
fieldzone                                                                
Allans 06 - 1  2021-07-29  Allans 06    1      13.0              11.96   
Allans 06 - 1  2021-07-29  Allans 06    1      14.0              12.88   
Allans 06 - 1  2021-07-29  Allans 06    1       8.0               7.36   
Allans 06 - 1  2021-07-29  Allans 06    1      10.0               9.20   
Allans 06 - 1  2021-07-29  Allans 06    1       7.0               6.44   

                            fieldzonedate field_join  zone_join planting_date  \
fieldzone                                                                       
Allans 06 - 1  Allans 06 - 1 - 2021-07-29  Allans 06          1    2021-04-10   
Allans 06 - 1  Allans 06 - 1 - 2021-07-29  Allans 06          1    2021-04-10   
Allans 06 - 1  Allans 06 - 1 - 2021-07-29  Allans 06          1    2021-04-10   
Allans 06 - 1  Allans 06 - 1 - 2021-07-29  Allans 06          1    2021-04-10   
Allans 06 - 1  Allans 06 - 1 - 2021-07-29  Allans 06          1    2021-04-10   

               variety   method        inputs protection  planting_rate  sand  \
fieldzone                                                                       
Allans 06 - 1  Krypton  Drilled  Conventional     Barley         262270    40   
Allans 06 - 1  Krypton  Drilled  Conventional     Barley         262270    40   
Allans 06 - 1  Krypton  Drilled  Conventional     Barley         262270    40   
Allans 06 - 1  Krypton  Drilled  Conventional     Barley         262270    40   
Allans 06 - 1  Krypton  Drilled  Conventional     Barley         262270    40   

               silt  clay  organic_matter harvest_date         fieldvariety  \
fieldzone                                                                     
Allans 06 - 1    41    19            24.6          NaT  Allans 06 - Krypton   
Allans 06 - 1    41    19            24.6          NaT  Allans 06 - Krypton   
Allans 06 - 1    41    19            24.6          NaT  Allans 06 - Krypton   
Allans 06 - 1    41    19            24.6          NaT  Allans 06 - Krypton   
Allans 06 - 1    41    19            24.6          NaT  Allans 06 - Krypton   

                               fieldvarietydate  heat_units  solar_radiation  
fieldzone                                                                     
Allans 06 - 1  Allans 06 - Krypton - 2021-07-29           0                0  
Allans 06 - 1  Allans 06 - Krypton - 2021-07-29           0                0  
Allans 06 - 1  Allans 06 - Krypton - 2021-07-29           0                0  
Allans 06 - 1  Allans 06 - Krypton - 2021-07-29           0                0  
Allans 06 - 1  Allans 06 - Krypton - 2021-07-29           0                0

In [16]:
summary_data = summary_data.reset_index(inplace=False)
summary_data = summary_data.drop(columns=['field_join', 'zone_join'], inplace=False)
summary_data.head()

fieldzone sample_date      field zone  diameter  stripped_diameter  \
0  Allans 06 - 1  2021-07-29  Allans 06    1      13.0              11.96   
1  Allans 06 - 1  2021-07-29  Allans 06    1      14.0              12.88   
2  Allans 06 - 1  2021-07-29  Allans 06    1       8.0               7.36   
3  Allans 06 - 1  2021-07-29  Allans 06    1      10.0               9.20   
4  Allans 06 - 1  2021-07-29  Allans 06    1       7.0               6.44   

                fieldzonedate planting_date  variety   method        inputs  \
0  Allans 06 - 1 - 2021-07-29    2021-04-10  Krypton  Drilled  Conventional   
1  Allans 06 - 1 - 2021-07-29    2021-04-10  Krypton  Drilled  Conventional   
2  Allans 06 - 1 - 2021-07-29    2021-04-10  Krypton  Drilled  Conventional   
3  Allans 06 - 1 - 2021-07-29    2021-04-10  Krypton  Drilled  Conventional   
4  Allans 06 - 1 - 2021-07-29    2021-04-10  Krypton  Drilled  Conventional   

  protection  planting_rate  sand  silt  clay  organic_matter harvest_date  \
0     Barley         262270    40    41    19            24.6          NaT   
1     Barley         262270    40    41    19            24.6          NaT   
2     Barley         262270    40    41    19            24.6          NaT   
3     Barley         262270    40    41    19            24.6          NaT   
4     Barley         262270    40    41    19            24.6          NaT   

          fieldvariety                  fieldvarietydate  heat_units  \
0  Allans 06 - Krypton  Allans 06 - Krypton - 2021-07-29           0   
1  Allans 06 - Krypton  Allans 06 - Krypton - 2021-07-29           0   
2  Allans 06 - Krypton  Allans 06 - Krypton - 2021-07-29           0   
3  Allans 06 - Krypton  Allans 06 - Krypton - 2021-07-29           0   
4  Allans 06 - Krypton  Allans 06 - Krypton - 2021-07-29           0   

   solar_radiation  
0                0  
1                0  
2                0  
3                0  
4                0

In [17]:
def skewness(series):
    return ss.skew(series, bias = False)

def kurt(series):
    return ss.kurtosis(series, bias = False)

In [18]:
summary_data_avg = summary_data.copy()

summary_data_avg = summary_data_avg.groupby(['fieldzonedate']).agg({'stripped_diameter' : ['mean', 'std', 'count', skewness, kurt],
                                                                'method' : ['first'],
                                                                'inputs' : ['first'],
                                                                'variety' : ['first'],
                                                                'protection' : ['first'],
                                                                'sand' : ['mean'],
                                                                'silt' : ['mean'],
                                                                'clay' : ['mean'],
                                                                'organic_matter' : ['mean'],
                                                                'planting_date' : ['first'],
                                                                'sample_date' : ['first'],
                                                                'fieldzone' : ['first']}).reset_index()

summary_data_avg.columns = ['fieldzonedate',
                            'mean_diameter',
                            'std_dev_diameter',
                            'pp2m2',
                            'skewness',
                            'kurtosis',
                            'method',
                            'inputs',
                            'variety',
                            'protection',
                            'sand',
                            'silt',
                            'clay',
                            'organic_matter',
                            'planting_date',
                            'sample_date',
                            'fieldzone']

summary_data_avg['d_lin'] = (summary_data_avg['mean_diameter'])**linearisation_coef
summary_data_avg['s_lin'] = (summary_data_avg['std_dev_diameter'])**linearisation_coef
summary_data_avg['heat_units'] = 0
summary_data_avg['solar_radiation'] = 0

summary_data_avg.tail()

fieldzonedate  mean_diameter  std_dev_diameter  pp2m2  \
3353  Wissey O (S) - 1 - 2019-09-19      34.209474          5.277874     38   
3354  Wissey O (S) - 2 - 2019-07-30      18.447179          3.409484     39   
3355  Wissey O (S) - 2 - 2019-09-19      30.631818          4.797228     44   
3356  Wissey O (S) - 3 - 2019-07-30      20.079000          2.996661     40   
3357  Wissey O (S) - 3 - 2019-09-19      29.920909          3.829350     44   

      skewness  kurtosis   method        inputs  variety protection  sand  \
3353 -0.366295 -0.436126  Drilled  Conventional  Shafton     Barley    11   
3354  0.261426  0.527252  Drilled  Conventional  Shafton     Barley    11   
3355 -0.065718 -0.292600  Drilled  Conventional  Shafton     Barley    11   
3356  0.333063 -0.493385  Drilled  Conventional  Shafton     Barley    11   
3357 -0.133634 -0.709054  Drilled  Conventional  Shafton     Barley    11   

      silt  clay  organic_matter planting_date sample_date         fieldzone  \
3353    64    25            71.2    2019-03-26  2019-09-19  Wissey O (S) - 1   
3354    64    25            71.2    2019-03-26  2019-07-30  Wissey O (S) - 2   
3355    64    25            71.2    2019-03-26  2019-09-19  Wissey O (S) - 2   
3356    64    25            71.2    2019-03-26  2019-07-30  Wissey O (S) - 3   
3357    64    25            71.2    2019-03-26  2019-09-19  Wissey O (S) - 3   

         d_lin     s_lin  heat_units  solar_radiation  
3353  9.095812  2.828374           0                0  
3354  6.183099  2.152437           0                0  
3355  8.489028  2.664520           0                0  
3356  6.519493  1.985631           0                0  
3357  8.365352  2.314479           0                0

In [19]:
weather_data_avg = weather_data.copy()

weather_data_avg = weather_data_avg.groupby(['date']).agg({'rain' : ['sum'],
                                                       'heat_units' : ['sum'],
                                                       'solar_radiation' : ['sum'],
                                                       'wind_speed_avg' : ['mean'],
                                                       'rh' : ['mean'],
                                                       'avg_temp' : ['mean']}).reset_index()

weather_data_avg.columns = ['date',
                            'rain',
                            'heat_units',
                            'solar_radiation',
                            'wind_speed_avg',
                            'rh',
                            'avg_temp']

weather_data_avg['day'] = weather_data_avg.date.dt.day
weather_data_avg['month'] = weather_data_avg.date.dt.month
weather_data_avg['day_month'] = weather_data_avg['day'].astype(str) + " - " + weather_data_avg['month'].astype(str)  

weather_data_avg_group = weather_data_avg.copy()

weather_data_avg_group = weather_data_avg_group.groupby(['day_month']).agg({'rain' : ['mean'],
                                                                            'heat_units' : ['mean'],
                                                                            'solar_radiation' : ['mean'],
                                                                            'wind_speed_avg' : ['mean'],
                                                                            'rh' : ['mean'],
                                                                            'avg_temp' : ['mean']}).reset_index()

weather_data_avg_group.columns = ['day_month',
                                  'rain',
                                  'heat_units',
                                  'solar_radiation',
                                  'wind_speed_avg',
                                  'rh',
                                  'avg_temp']

max_date = max(weather_data_avg.date)

for i in range(1, 300):
    
    clear_output(wait=True)
    
    date = max_date + timedelta(days=i)
    weather_data_avg = weather_data_avg.append({'date': date,
                                                'rain': np.nan,
                                                'heat_units':np.nan,
                                                'solar_radiation':np.nan,
                                                'wind_speed_avg':np.nan,
                                                'rh':np.nan,
                                                'avg_temp':np.nan }, ignore_index=True)
    
    print("Current Progress:", np.round(i/300*100,0),"%")
    
weather_data_avg['day'] = weather_data_avg.date.dt.day
weather_data_avg['month'] = weather_data_avg.date.dt.month
weather_data_avg['day_month'] = weather_data_avg['day'].astype(str) + " - " + weather_data_avg['month'].astype(str)  

Current Progress: 100.0 %


In [20]:
###THIS IS A VERY SLOW PROCESS (COULD PARALLEL PROCESSING BE INTRODUCED)

def mean_weather(day_month, variable):
    df = weather_data_avg_group[weather_data_avg_group['day_month']==day_month]
    weather_value = df[variable].sum()
    return weather_value

for variable in ['rain', 'heat_units', 'solar_radiation', 'wind_speed_avg', 'rh', 'avg_temp']:
    for i in weather_data_avg.index:
        
        clear_output(wait=True)
        
        if weather_data_avg[variable][i] == np.nan:
            test = 'test'
            
        else:
            day_month = weather_data_avg['day_month'][i]
            weather_data_avg[variable][i] = mean_weather(day_month, variable)
            
        print(f"{variable} progress:", np.round(i/len(weather_data_avg)*100,0),"%")
    
weather_data_avg.tail()

avg_temp progress: 100.0 %


date    rain  heat_units  solar_radiation  wind_speed_avg  \
3038 2022-09-07  0.4250   34.302083         6216.560        2.562083   
3039 2022-09-08  0.9500   29.063021         6372.230        3.309219   
3040 2022-09-09  0.9125   11.608333         6479.035        3.017396   
3041 2022-09-10  0.6875   10.983333         6113.860        3.051042   
3042 2022-09-11  0.7625   11.714063         5075.020        4.284167   

             rh   avg_temp  day  month day_month  
3038  82.467708  14.387500    7      9     7 - 9  
3039  83.462500  14.856250    8      9     8 - 9  
3040  85.604688  14.608333    9      9     9 - 9  
3041  83.671875  13.983333   10      9    10 - 9  
3042  85.128646  14.714062   11      9    11 - 9

In [21]:
weather_data_avg

date       rain  heat_units  solar_radiation  wind_speed_avg  \
0    2014-05-14   0.825000    6.506771      9217.820000        4.122604   
1    2014-05-15   0.925000    8.078125     11512.520000        3.593802   
2    2014-05-16   0.425000    9.312500      9943.060000        4.079896   
3    2014-05-17   4.650000    9.153125      9964.665000        3.792969   
4    2014-05-18   5.850000    9.229167     10198.580000        3.074792   
5    2014-05-19   0.875000    9.851562     11232.215000        3.850104   
6    2014-05-20   0.825000   10.395312     10693.015000        5.160990   
7    2014-05-21   0.525000   10.948438     11017.475000        8.278646   
8    2014-05-22   1.675000   10.759375     11270.720000        4.674531   
9    2014-05-23   0.450000    9.909375     11287.270000        5.625417   
10   2014-05-24   2.275000   10.091667     10252.590000        4.455833   
11   2014-05-25   0.000000   10.326563      9961.955000        4.786094   
12   2014-05-26   0.050000   11.153125     10688.685000        4.330312   
13   2014-05-27   3.950000   11.326042     10705.695000        3.724479   
14   2014-05-28   1.350000   10.816667     10533.250000        2.861875   
15   2014-05-29   1.700000   10.259375      9161.865000        3.753854   
16   2014-05-30   0.050000   11.020833      9663.945000        4.837917   
17   2014-05-31   3.950000   11.275521      9459.030000        4.417917   
18   2014-06-01   0.400000   12.456250     11261.765000        4.044167   
19   2014-06-02   0.800000   21.543229      9338.925000        4.710729   
20   2014-06-03   0.300000   11.832812      9973.485000        3.026406   
21   2014-06-04   2.025000    9.961458      7797.465000        3.726823   
22   2014-06-05   1.100000   10.951042     10164.325000        2.964115   
23   2014-06-06   2.625000   10.465625     11540.495000        2.767031   
24   2014-06-07   2.075000   11.464063     10508.750000        3.380521   
25   2014-06-08   0.500000   11.408854     10507.620000        2.761823   
26   2014-06-09   0.125000   11.489063     11075.940000        2.899010   
27   2014-06-10   2.250000   11.829688      9391.565000        3.502760   
28   2014-06-11   1.250000   12.640104     10717.525000        4.509323   
29   2014-06-12   1.250000   12.550521      9477.655000        3.659792   
30   2014-06-13   1.750000   15.821354     10095.180000        2.397396   
31   2014-06-14   1.075000   13.285417      9506.890000        4.221562   
32   2014-06-15   0.225000   12.329687     12014.545000        2.865104   
33   2014-06-16   1.250000   18.456250     10205.630000        2.964062   
34   2014-06-17   2.050000   22.019792      9634.385000        3.728646   
35   2014-06-18   7.550000   38.610417      8641.240000        5.662812   
36   2014-06-19   0.800000   38.680208      8548.475000        3.539531   
37   2014-06-20   2.750000   24.722917      8851.315000        4.384219   
38   2014-06-21   0.200000   26.986458     11084.435000        5.183958   
39   2014-06-22   2.037500   12.194792     10174.560000        5.103385   
40   2014-06-23   2.462500   13.070833     10612.765000        2.514323   
41   2014-06-24   0.587500   37.426562     11151.445000        2.699219   
42   2014-06-25   1.462500   45.523958     10364.580000        3.911979   
43   2014-06-26   0.512500   33.630208     11428.085000        4.907812   
44   2014-06-27   5.825000   12.978125      9533.070000        5.702708   
45   2014-06-28   5.725000   11.884896      8344.095000        4.562812   
46   2014-06-29   1.450000   32.541146      9233.205000        4.496823   
47   2014-06-30   0.200000   24.852083     11026.275000        4.181927   
48   2014-07-01   0.550000   45.520312     11067.635000        3.625365   
49   2014-07-02   0.025000   13.616667     12443.735000        2.707135   
50   2014-07-03   0.300000   13.915625     12028.410000        2.762656   
51   2014-07-04   3.250000   17.865625     11558.690000        3.098229   
52   2014-07-05   0.950000   29.1020

In [22]:
def cum_heat_units(start, finish, weather_data):
    df = weather_data.loc[(weather_data['date'] > start) & (weather_data['date'] < finish), ['heat_units']]
    total_hu = df['heat_units'].sum()
    return total_hu

def cum_solar_radiation(start, finish, weather_data):
    df = weather_data.loc[(weather_data['date'] > start) & (weather_data['date'] < finish), ['solar_radiation']]
    total_sr = df['solar_radiation'].sum()
    return total_sr

In [23]:
for i in summary_data_avg.index:
    clear_output(wait=True)
    
    planting_date = summary_data_avg['planting_date'][i]
    sample_date = summary_data_avg['sample_date'][i]
    summary_data_avg['solar_radiation'][i] = cum_solar_radiation(planting_date, sample_date, weather_data_avg)
    
    print("Current Progress:", np.round(i/len(summary_data_avg)*100,0),"%")

Current Progress: 100.0 %


In [24]:
for i in summary_data_avg.index:
    clear_output(wait=True)
    
    planting_date = summary_data_avg['planting_date'][i]
    sample_date = summary_data_avg['sample_date'][i]
    summary_data_avg['heat_units'][i] = cum_heat_units(planting_date, sample_date, weather_data_avg)
    
    print("Current Progress:", np.round(i/len(summary_data_avg)*100,0),"%")

Current Progress: 100.0 %


def heat_units_received(summary_data_avg):
    for i in summary_data_avg.index:
        clear_output(wait=True)
        planting_date = summary_data_avg['planting_date'][i]
        sample_date = summary_data_avg['sample_date'][i]
        summary_data_avg['heat_units'][i] = cum_heat_units(planting_date, sample_date, weather_data_avg)
        print("Current Progress:", np.round(i/len(summary_data_avg)*100,0),"%")


def process_chunk(proc_chunk):
    """
    Process the partial array/dataframe `proc_chunk` passed to this process worker.
    Return an array/dataframe of the same length and same indices.
    """

    chunk_res = heat_units_received(proc_chunk)
    chunk_res.index = proc_chunk.index
    
    return chunk_res

# set the number of processes
n_proc = mp.cpu_count()

# this often can't be devided evenly (handle this in the for-loop below)
chunksize = len(summary_data_avg.index) // n_proc

# devide into chunks
proc_chunks = []
for i_proc in range(n_proc):
    chunkstart = i_proc * chunksize
    # make sure to include the division remainder for the last process
    chunkend = (i_proc + 1) * chunksize if i_proc < n_proc - 1 else None

    proc_chunks.append(summary_data_avg.iloc[slice(chunkstart, chunkend)])

assert sum(map(len, proc_chunks)) == len(summary_data_avg.index)   # make sure all data is in the chunks

print('x')

# distribute work to the worker processes
with mp.Pool(processes=n_proc) as pool:
    # starts the sub-processes without blocking
    # pass the chunk to each worker process
    proc_results = [pool.apply_async(process_chunk, args=(chunk,)) for chunk in proc_chunks]

    # blocks until all results are fetched
    result_chunks = [r.get() for r in proc_results]

    # concatenate results from worker processes
    results = pd.concat(result_chunks)
    
print('x')

results = pd.concat((summary_data_avg, results), axis=1)
assert len(results) == len(summary_data_avg.index)   # make sure we got a result for each coordinate pair

In [25]:
summary_data_avg['protection_2'] = summary_data_avg['protection'].copy()
summary_data_avg = pd.get_dummies(summary_data_avg, columns = ['protection_2'], drop_first = False)

In [26]:
summary_data_avg.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 3358 entries, 0 to 3357
Data columns (total 25 columns):
 #   Column               Non-Null Count  Dtype         
---  ------               --------------  -----         
 0   fieldzonedate        3358 non-null   object        
 1   mean_diameter        3358 non-null   float64       
 2   std_dev_diameter     3358 non-null   float64       
 3   pp2m2                3358 non-null   int64         
 4   skewness             3358 non-null   float64       
 5   kurtosis             3358 non-null   float64       
 6   method               3358 non-null   object        
 7   inputs               3358 non-null   object        
 8   variety              3358 non-null   object        
 9   protection           3358 non-null   object        
 10  sand                 3358 non-null   int64         
 11  silt                 3358 non-null   int64         
 12  clay                 3358 non-null   int64         
 13  organic_matter       3358 non-nul

In [27]:
summary_data_avg[summary_data_avg.isna().any(axis=1)]

Empty DataFrame
Columns: [fieldzonedate, mean_diameter, std_dev_diameter, pp2m2, skewness, kurtosis, method, inputs, variety, protection, sand, silt, clay, organic_matter, planting_date, sample_date, fieldzone, d_lin, s_lin, heat_units, solar_radiation, protection_2_Barley, protection_2_Fleece, protection_2_None, protection_2_Poly]
Index: []

In [28]:
summary_data_avg = summary_data_avg.dropna()

In [29]:
def average_count(fieldzone, df_1 = summary_data_avg):
    
    df_1 = df_1[df_1['fieldzone']==fieldzone]
    average_count = df_1['pp2m2'].mean()
    
    if mt.isnan(average_count):
        average_count = 40
      
    return average_count

average_count('RH33 - 1')

36.333333333333336

In [30]:
def max_sample_date(fieldzone, df_1 = summary_data_avg, df_2 = zone_data):
    
    df_1 = df_1[df_1['fieldzone'] == fieldzone]
    max_sample_date = max(df_1['sample_date'], default = 0)
    if max_sample_date == 0:
        df_2 = df_2[df_2['fieldzone'] == fieldzone]
        max_sample_date = df_2['planting_date'].max()
    
    return max_sample_date

max_sample_date('RH33 - 1')

Timestamp('2021-11-18 00:00:00')

In [31]:
def max_mean_diameter_lin(fieldzone, df_1 = summary_data_avg):
    
    df_1 = df_1[df_1['fieldzone']==fieldzone]
    max_mean_diameter = df_1['mean_diameter'].max()
    max_mean_diameter_lin = max_mean_diameter ** linearisation_coef
    
    if mt.isnan(max_mean_diameter_lin):
        max_mean_diameter_lin = 0
    
    return max_mean_diameter_lin

max_mean_diameter_lin('Allans 07 - 1')

9.26293214352213

In [32]:
def max_std_dev_diameter_lin(fieldzone, df_1 = summary_data_avg):
    
    df_1 = df_1[df_1['fieldzone']==fieldzone]
    max_std_dev_diameter = df_1['std_dev_diameter'].max()
    max_std_dev_diameter_lin = max_std_dev_diameter ** linearisation_coef
    
    if mt.isnan(max_std_dev_diameter_lin):
        max_std_dev_diameter_lin = 0
    
    return max_std_dev_diameter_lin

max_std_dev_diameter_lin('Allans 07 - 1')

4.348294771174176

In [33]:
def max_solar(fieldzone, df_1 = summary_data_avg):
    
    df_1 = df_1[df_1['fieldzone']==fieldzone]
    max_solar = df_1['solar_radiation'].max()
    
    if mt.isnan(max_solar):
        max_solar = 0
    
    return max_solar

max_solar('Allans 07 - 1')

1761357

In [34]:
def max_heat(fieldzone, df_1 = summary_data_avg):
    
    df_1 = df_1[df_1['fieldzone']==fieldzone]
    max_heat = df_1['heat_units'].max()
    
    if mt.isnan(max_heat):
        max_heat = 0
    
    return max_heat

max_heat('Allans 07 - 1')

4079

In [35]:
def filter_data(data, method, inputs, variety):
    
    filtered = data[data['variety'].str.contains(variety)]
    filtered = filtered[filtered['inputs'].str.contains(inputs)]
    filtered = filtered[filtered['method'].str.contains(method)]
    
    return filtered

In [36]:
def predict_weather(start, finish, variable, df_1 = weather_data):
    
    df_1 = df_1.loc[(df_1['date'] > start) & (df_1['date'] < finish), [variable]]
    predicted_weather= df_1[variable].sum()
    
    return predicted_weather

start = datetime(year=2021, month=6, day=2, hour=13, minute=14, second=31)
finish = datetime(year=2022, month=6, day=2, hour=13, minute=14, second=31)

predict_weather(start, finish, 'rain')

363.0

In [37]:
zone_data['mean_pp2m2'] = 0.0
zone_data['max_sample_date'] = 0
zone_data['max_mean_diameter_lin'] = 0.0
zone_data['max_std_dev_diameter_lin'] = 0.0
zone_data['max_heat'] = 0.0
zone_data['max_solar'] = 0.0
zone_data['remaining_heat'] = 0.0
zone_data['remaining_solar'] = 0.0

for i in zone_data.index:
    
    clear_output(wait=True)
    
    fieldzone = zone_data.loc[i, 'fieldzone']
    zone_data.loc[i, 'mean_pp2m2'] = average_count(fieldzone)
    zone_data.loc[i, 'max_sample_date'] = max_sample_date(fieldzone)
    zone_data.loc[i, 'max_mean_diameter_lin'] = max_mean_diameter_lin(fieldzone)
    zone_data.loc[i, 'max_std_dev_diameter_lin'] = max_std_dev_diameter_lin(fieldzone)
    zone_data.loc[i, 'max_heat'] = max_heat(fieldzone)
    zone_data.loc[i, 'max_solar'] = max_solar(fieldzone)
    start = zone_data.loc[i, 'max_sample_date']
    today = datetime.today() + timedelta(days=future_days)
    finish = today.strftime("%d/%m/%Y")
    zone_data.loc[i, 'remaining_heat'] = cum_heat_units(start, finish, weather_data_avg)
    zone_data.loc[i, 'remaining_solar'] = cum_solar_radiation(start, finish, weather_data_avg)   
    
    print("Current Progress:", np.round(i/len(zone_data)*100,0),"%")
    
zone_data['establishment'] = (zone_data['mean_pp2m2']/2*10000)/zone_data['planting_rate']
zone_data['est_mean_diameter_gain'] = 0.0
zone_data['est_std_dev_diameter_gain'] = 0.0
zone_data['est_mean_diameter'] = 0.0
zone_data['est_std_dev_diameter'] = 0.0


Current Progress: 100.0 %


In [39]:
summary_data_avg.sort_values(by='mean_diameter', ascending=False)

fieldzonedate  mean_diameter  \
397          Garretts Decoy 3 - 3 - 2019-11-19      40.725333   
2359             Park Farm 50 - 1 - 2019-11-25      38.477647   
400          Garretts Decoy 3 - 4 - 2019-11-19      37.996000   
394          Garretts Decoy 3 - 2 - 2019-11-19      37.260000   
391          Garretts Decoy 3 - 1 - 2019-11-19      37.076000   
37                  Allans 07 - 2 - 2020-01-13      36.267368   
962                  HH30/31A - 1 - 2020-02-19      35.715714   
33                  Allans 07 - 1 - 2020-01-13      35.220667   
2412             Park Farm 55 - 1 - 2020-11-24      35.068235   
32                  Allans 07 - 1 - 2019-10-29      35.047619   
2165             Park Farm 28 - 2 - 2020-03-10      34.618286   
2362             Park Farm 50 - 2 - 2019-11-25      34.441026   
2243             Park Farm 31 - 3 - 2021-10-14      34.390476   
3353             Wissey O (S) - 1 - 2019-09-19      34.209474   
562       Grotec Big Vicarage - 1 - 2020-01-30      34.205128   
3246                Wissey 33 - 2 - 2019-09-30      34.100000   
3096         Symmingtons HF1 - 16 - 2020-11-26      34.040000   
2249             Park Farm 31 - 4 - 2021-10-14      33.920000   
328     Chatteris Farms 07/08 - 4 - 2021-02-16      33.917333   
2419             Park Farm 55 - 2 - 2020-11-24      33.791351   
3157         Symmingtons HF4N - 3 - 2019-12-19      33.773684   
649            Grotec Long 15 - 6 - 2020-11-24      33.718000   
2237             Park Farm 31 - 2 - 2021-10-14      33.562963   
572       Grotec Big Vicarage - 4 - 2020-01-30      33.198857   
2163             Park Farm 28 - 2 - 2020-01-09      33.196667   
634            Grotec Long 15 - 3 - 2020-11-24      33.011765   
2434             Park Farm 55 - 4 - 2021-01-06      32.991628   
308     Chatteris Farms 07/08 - 1 - 2021-01-11      32.936000   
2231             Park Farm 31 - 1 - 2021-10-14      32.785455   
282     Buckenham Long Narrow - 4 - 2021-11-19      32.743636   
1622          Lords Ground 57 - 2 - 2021-08-16      32.704516   
272     Buckenham Long Narrow - 2 - 2021-11-19      32.677037   
773                 Guyers 17 - 5 - 2021-11-05      32.674839   
3154         Symmingtons HF4N - 2 - 2020-02-27      32.673143   
2164             Park Farm 28 - 2 - 2020-02-13      32.608889   
584       Grotec Big Vicarage - 7 - 2020-01-30      32.568000   
2344             Park Farm 47 - 3 - 2019-12-20      32.555455   
568       Grotec Big Vicarage - 3 - 2019-12-04      32.506667   
2427             Park Farm 55 - 3 - 2021-01-06      32.466316   
779                 Guyers 17 - 6 - 2021-11-05      32.327778   
3069         Symmingtons HF1 - 11 - 2020-11-26      32.292000   
302   Buckenham Stadium Field - 4 - 2021-11-19      32.292000   
2347             Park Farm 47 - 4 - 2019-12-20      32.237551   
1654          Lords Ground 63 - 5 - 2020-07-22      32.200000   
644            Grotec Long 15 - 5 - 2020-11-24      32.163200   
3250                Wissey 36 - 2 - 2019-09-30      32.129231   
2160             Park Farm 28 - 1 - 2020-02-13      32.108000   
1650          Lords Ground 63 - 4 - 2020-07-22      32.004848   
363       Chatteris Farms 27B - 4 - 2020-01-20      31.951351   
2255             Park Farm 31 - 5 - 2021-10-14      31.855000   
2170             Park Farm 28 - 3 - 2020-03-10      31.832000   
2549                 RH34/35A - 6 - 2021-03-04      31.825185   
817                 Guyers 26 - 2 - 2020-10-15      31.770667   
3258             Wissey F (S) - 2 - 2020-01-30      31.740000   
3158         Symmingtons HF4N - 3 - 2020-01-28      31.715789   
3244                Wissey 33 - 1 - 2019-09-30      31.600930   
2254             Park Farm 31 - 5 - 2021-09-29      31.574400   
805                 Guyers 20 - 4 - 2020-11-25      31.530909   
1140                     HH46 - 5 - 2021-04-06      31.468182   
2175             Park Farm 28 - 4 - 2020-03-10      31.449474   
352       Chatteris Farms 27B - 1 - 2020-02-21      31.388235   
321